# Machine Translation using OpenNMT

# Jamo and Char Tokenization

In [1]:
cd /home/ubuntu/MT

/home/ubuntu/MT


In [3]:
!pip install hgtk

Looking in indexes: http://ftp.daumkakao.com/pypi/simple
  Created wheel for hgtk: filename=hgtk-0.1.3-py2.py3-none-any.whl size=6689 sha256=c79e1449aa15b61035cead5f6ce27dcce6f4dc168f720c8444872605bbc5f22e
  Stored in directory: /home/ubuntu/.cache/pip/wheels/96/10/4b/0887dcaf5e0b0d26b807fef3497703fea2c44a76f91d198bd3
Successfully built hgtk


In [2]:
!python OpenNMT-py/tools/learn_bpe.py -i OpenNMT-py/Data/src-train.txt -o OpenNMT-py/Data/src.code -s 32000

In [4]:
!python OpenNMT-py/tools/apply_morph_ko.py -i OpenNMT-py/Data/src-train.txt -o OpenNMT-py/Data/src-train-morph.txt
!python OpenNMT-py/tools/apply_morph_ko.py -i OpenNMT-py/Data/src-valid.txt -o OpenNMT-py/Data/src-val-morph.txt
!python OpenNMT-py/tools/apply_morph_ko.py -i OpenNMT-py/Data/src-test.txt -o OpenNMT-py/Data/src-test-morph.txt

In [3]:
!python OpenNMT-py/tools/apply_bpe.py -c OpenNMT-py/Data/src.code -i OpenNMT-py/Data/src-train.txt -o OpenNMT-py/Data/src-train-bpe.txt
!python OpenNMT-py/tools/apply_bpe.py -c OpenNMT-py/Data/src.code -i OpenNMT-py/Data/src-valid.txt -o OpenNMT-py/Data/src-val-bpe.txt
!python OpenNMT-py/tools/apply_bpe.py -c OpenNMT-py/Data/src.code -i OpenNMT-py/Data/src-test.txt -o OpenNMT-py/Data/src-test-bpe.txt

# **Preprocess the data**

We will be working with some example data in data/ folder.

The data consists of parallel source (src) and target (tgt) data containing one sentence per line with tokens separated by a space:

1. src-train.txt

2. tgt-train.txt

3. src-val.txt

4. tgt-val.txt


Train data and validataion data are required for machine translation training.

Validation files are required and used to evaluate the convergence of the training. It usually contains no more than 5000 sentences.


> If you think about it briefly, you can specify the path of train data and validation data, and specify the path and name to save in -save_data.

> If you want to set vocab size add below command
<br>
-src_vocab_size 32000 -tgt_vocab_size 32000

The vocab size is usually 32000.

In [5]:
!python OpenNMT-py/preprocess.py -train_src OpenNMT-py/Data/src-train-bpe.txt -train_tgt OpenNMT-py/Data/tgt-train-morph.txt -valid_src OpenNMT-py/Data/src-val-bpe.txt -valid_tgt OpenNMT-py/Data/tgt-val-morph.txt -save_data OpenNMT-py/Data/bpe2morph/demo -src_vocab_size -1 -tgt_vocab_size -1 -overwrite

[2020-12-10 13:36:52,370 INFO] Extracting features...
[2020-12-10 13:36:52,370 INFO]  * number of source features: 0.
[2020-12-10 13:36:52,370 INFO]  * number of target features: 0.
[2020-12-10 13:36:52,370 INFO] Building `Fields` object...
[2020-12-10 13:36:52,370 INFO] Building & saving training data...
[2020-12-10 13:36:55,610 INFO] Building shard 0.
[2020-12-10 13:37:49,784 INFO]  * saving 0th train data shard to OpenNMT-py/Data/bpe2morph/demo.train.0.pt.
[2020-12-10 13:38:33,356 INFO]  * tgt vocab size: 160272.
[2020-12-10 13:38:33,422 INFO]  * src vocab size: 36974.
[2020-12-10 13:38:34,094 INFO] Building & saving validation data...
[2020-12-10 13:38:34,527 INFO] Building shard 0.
[2020-12-10 13:38:34,831 INFO]  * saving 0th valid data shard to OpenNMT-py/Data/bpe2morph/demo.valid.0.pt.


!python OpenNMT-py/preprocess.py -train_src OpenNMT-py/Data/src-train-bpe.txt -train_tgt OpenNMT-py/Data/tgt-train-bpe.txt -valid_src OpenNMT-py/Data/src-val-bpe.txt -valid_tgt OpenNMT-py/Data/tgt-val-bpe.txt -save_data OpenNMT-py/Data/demo -src_vocab_size 32000 -tgt_vocab_size 32000

# **Train the data(Transformer)**

https://papers.nips.cc/paper/7181-attention-is-all-you-need.pdf


> If you get GPU-related errors, try halving batch_size

**Below is the full command, and if you want to know more about it, search about Transformer.**

!python OpenNMT-py/train.py -data OpenNMT-py/data/demo -save_model OpenNMT-py/data/model/model -layers 6 -rnn_size 512 -word_vec_size 512 -transformer_ff 2048 -heads 8 -encoder_type transformer -decoder_type transformer -position_encoding -train_steps 200000 -max_generator_batches 2 -dropout 0.1 -batch_size 4096 -batch_type tokens -normalization tokens -accum_count 2 -optim adam -adam_beta2 0.998 -decay_method noam -warmup_steps 8000 -learning_rate 2 -max_grad_norm 0 -param_init 0 -param_init_glorot -label_smoothing 0.1 -valid_steps 1000 -save_checkpoint_steps 1000 -world_size 1 -gpu_rank 0  

In [1]:
!nvidia-smi

Thu Dec 10 13:33:29 2020       
+-----------------------------------------------------------------------------+
| NVIDIA-SMI 440.64       Driver Version: 440.64       CUDA Version: 10.2     |
|-------------------------------+----------------------+----------------------+
| GPU  Name        Persistence-M| Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp  Perf  Pwr:Usage/Cap|         Memory-Usage | GPU-Util  Compute M. |
|===============================+======================+======================|
|   0  Quadro RTX 6000     On   | 00000000:00:06.0 Off |                    0 |
| N/A   25C    P8    12W / 250W |      0MiB / 22698MiB |      0%      Default |
+-------------------------------+----------------------+----------------------+
                                                                               
+-----------------------------------------------------------------------------+
| Processes:                                                       GPU Memory |
|  GPU  

In [6]:
!python OpenNMT-py/train.py -data OpenNMT-py/Data/bpe2morph/demo -save_model OpenNMT-py/Data/bpe2morph/model/model -layers 6 -rnn_size 512 -word_vec_size 512 -transformer_ff 2048 -heads 8 -encoder_type transformer -decoder_type transformer -position_encoding -train_steps 50000 -max_generator_batches 2 -dropout 0.1 -batch_size 4096 -batch_type tokens -normalization tokens -accum_count 2 -optim adam -adam_beta2 0.998 -decay_method noam -warmup_steps 8000 -learning_rate 2 -max_grad_norm 0 -param_init 0 -param_init_glorot -label_smoothing 0.1 -valid_steps 1000 -save_checkpoint_steps 10000 -world_size 1 -gpu_rank 0 -tensorboard -tensorboard_log_dir 'logs/my_board/bpe2morph'

[2020-12-10 13:38:37,905 INFO]  * src vocab size = 36974
[2020-12-10 13:38:37,905 INFO]  * tgt vocab size = 160272
[2020-12-10 13:38:37,905 INFO] Building model...
[2020-12-10 13:38:48,131 INFO] NMTModel(
  (encoder): TransformerEncoder(
    (embeddings): Embeddings(
      (make_embedding): Sequential(
        (emb_luts): Elementwise(
          (0): Embedding(36974, 512, padding_idx=1)
        )
        (pe): PositionalEncoding(
          (dropout): Dropout(p=0.1, inplace=False)
        )
      )
    )
    (transformer): ModuleList(
      (0): TransformerEncoderLayer(
        (self_attn): MultiHeadedAttention(
          (linear_keys): Linear(in_features=512, out_features=512, bias=True)
          (linear_values): Linear(in_features=512, out_features=512, bias=True)
          (linear_query): Linear(in_features=512, out_features=512, bias=True)
          (softmax): Softmax(dim=-1)
          (dropout): Dropout(p=0.1, inplace=False)
          (final_linear): Linear(in_features=512, out_fea

[2020-12-10 13:38:48,234 INFO] Starting training on GPU: [0]
[2020-12-10 13:38:48,234 INFO] Start training loop and validate every 1000 steps...
[2020-12-10 13:38:48,234 INFO] Loading dataset from OpenNMT-py/Data/bpe2morph/demo.train.0.pt
[2020-12-10 13:39:22,127 INFO] number of examples: 691580
[2020-12-10 13:40:23,261 INFO] Step 50/50000; acc:   2.22; ppl: 32351.80; xent: 10.38; lr: 0.00001; 3026/4235 tok/s;     95 sec
[2020-12-10 13:41:18,320 INFO] Step 100/50000; acc:   6.35; ppl: 24438.76; xent: 10.10; lr: 0.00001; 5096/7369 tok/s;    150 sec
[2020-12-10 13:42:13,352 INFO] Step 150/50000; acc:   6.28; ppl: 15590.14; xent: 9.65; lr: 0.00002; 5177/7365 tok/s;    205 sec
[2020-12-10 13:43:08,381 INFO] Step 200/50000; acc:   6.26; ppl: 8110.41; xent: 9.00; lr: 0.00002; 5056/7343 tok/s;    260 sec
[2020-12-10 13:44:03,610 INFO] Step 250/50000; acc:   6.17; ppl: 3913.27; xent: 8.27; lr: 0.00003; 5244/7230 tok/s;    315 sec
[2020-12-10 13:44:58,394 INFO] Step 300/50000; acc:   6.19; ppl:

[2020-12-10 14:35:01,998 INFO] Step 2950/50000; acc:  42.65; ppl: 20.23; xent: 3.01; lr: 0.00036; 5056/7336 tok/s;   3374 sec
[2020-12-10 14:35:56,780 INFO] Step 3000/50000; acc:  42.23; ppl: 20.91; xent: 3.04; lr: 0.00037; 5290/7369 tok/s;   3429 sec
[2020-12-10 14:35:56,782 INFO] Loading dataset from OpenNMT-py/Data/bpe2morph/demo.valid.0.pt
[2020-12-10 14:35:57,224 INFO] number of examples: 8014
[2020-12-10 14:36:15,857 INFO] Validation perplexity: 26.6524
[2020-12-10 14:36:15,858 INFO] Validation accuracy: 44.5383
[2020-12-10 14:37:11,151 INFO] Step 3050/50000; acc:  44.10; ppl: 18.17; xent: 2.90; lr: 0.00038; 3734/5456 tok/s;   3503 sec
[2020-12-10 14:38:05,951 INFO] Step 3100/50000; acc:  43.67; ppl: 19.07; xent: 2.95; lr: 0.00038; 5224/7291 tok/s;   3558 sec
[2020-12-10 14:39:01,033 INFO] Step 3150/50000; acc:  44.62; ppl: 17.86; xent: 2.88; lr: 0.00039; 5176/7354 tok/s;   3613 sec
[2020-12-10 14:39:56,117 INFO] Step 3200/50000; acc:  45.44; ppl: 16.67; xent: 2.81; lr: 0.00040; 

[2020-12-10 15:30:07,935 INFO] Step 5850/50000; acc:  60.46; ppl:  5.85; xent: 1.77; lr: 0.00072; 5144/7364 tok/s;   6680 sec
[2020-12-10 15:31:03,419 INFO] Step 5900/50000; acc:  59.98; ppl:  6.10; xent: 1.81; lr: 0.00073; 5178/7290 tok/s;   6735 sec
[2020-12-10 15:31:58,274 INFO] Step 5950/50000; acc:  60.28; ppl:  5.95; xent: 1.78; lr: 0.00074; 5181/7306 tok/s;   6790 sec
[2020-12-10 15:32:53,465 INFO] Step 6000/50000; acc:  60.53; ppl:  5.84; xent: 1.76; lr: 0.00074; 5136/7355 tok/s;   6845 sec
[2020-12-10 15:32:53,468 INFO] Loading dataset from OpenNMT-py/Data/bpe2morph/demo.valid.0.pt
[2020-12-10 15:32:53,953 INFO] number of examples: 8014
[2020-12-10 15:33:12,656 INFO] Validation perplexity: 6.84747
[2020-12-10 15:33:12,656 INFO] Validation accuracy: 61.8195
[2020-12-10 15:34:07,649 INFO] Step 6050/50000; acc:  60.33; ppl:  5.90; xent: 1.77; lr: 0.00075; 3831/5442 tok/s;   6919 sec
[2020-12-10 15:35:02,514 INFO] Step 6100/50000; acc:  60.60; ppl:  5.77; xent: 1.75; lr: 0.00075; 

[2020-12-10 16:25:08,787 INFO] Step 8750/50000; acc:  64.61; ppl:  4.50; xent: 1.51; lr: 0.00094; 5203/7275 tok/s;   9981 sec
[2020-12-10 16:26:03,316 INFO] Step 8800/50000; acc:  64.51; ppl:  4.46; xent: 1.49; lr: 0.00094; 5260/7411 tok/s;  10035 sec
[2020-12-10 16:26:58,549 INFO] Step 8850/50000; acc:  65.07; ppl:  4.35; xent: 1.47; lr: 0.00094; 5037/7347 tok/s;  10090 sec
[2020-12-10 16:27:53,358 INFO] Step 8900/50000; acc:  64.72; ppl:  4.42; xent: 1.49; lr: 0.00094; 5250/7352 tok/s;  10145 sec
[2020-12-10 16:28:48,382 INFO] Step 8950/50000; acc:  64.69; ppl:  4.41; xent: 1.48; lr: 0.00093; 5300/7362 tok/s;  10200 sec
[2020-12-10 16:29:42,980 INFO] Step 9000/50000; acc:  64.51; ppl:  4.50; xent: 1.50; lr: 0.00093; 5334/7326 tok/s;  10255 sec
[2020-12-10 16:29:42,982 INFO] Loading dataset from OpenNMT-py/Data/bpe2morph/demo.valid.0.pt
[2020-12-10 16:29:43,423 INFO] number of examples: 8014
[2020-12-10 16:30:02,232 INFO] Validation perplexity: 5.35116
[2020-12-10 16:30:02,232 INFO] V

...

[2020-12-11 01:30:18,488 INFO] Step 37400/50000; acc:  80.01; ppl:  2.04; xent: 0.71; lr: 0.00046; 5164/7308 tok/s;  42690 sec
[2020-12-11 01:31:13,440 INFO] Step 37450/50000; acc:  80.17; ppl:  2.02; xent: 0.70; lr: 0.00046; 5135/7356 tok/s;  42745 sec
[2020-12-11 01:32:08,116 INFO] Step 37500/50000; acc:  80.38; ppl:  2.02; xent: 0.70; lr: 0.00046; 5280/7292 tok/s;  42800 sec
[2020-12-11 01:33:02,968 INFO] Step 37550/50000; acc:  79.97; ppl:  2.04; xent: 0.71; lr: 0.00046; 5116/7361 tok/s;  42855 sec
[2020-12-11 01:33:57,612 INFO] Step 37600/50000; acc:  80.20; ppl:  2.03; xent: 0.71; lr: 0.00046; 5344/7351 tok/s;  42909 sec
[2020-12-11 01:34:52,546 INFO] Step 37650/50000; acc:  80.13; ppl:  2.03; xent: 0.71; lr: 0.00046; 5182/7389 tok/s;  42964 sec
[2020-12-11 01:35:47,639 INFO] Step 37700/50000; acc:  80.13; ppl:  2.03; xent: 0.71; lr: 0.00046; 5121/7289 tok/s;  43019 sec
[2020-12-11 01:36:42,410 INFO] Step 37750/50000; acc:  80.41; ppl:  2.01; xent: 0.70; lr: 0.00045; 5160/7302 to

[2020-12-11 02:24:42,224 INFO] Step 40250/50000; acc:  80.80; ppl:  1.98; xent: 0.69; lr: 0.00044; 5216/7278 tok/s;  45954 sec
[2020-12-11 02:25:37,198 INFO] Step 40300/50000; acc:  80.83; ppl:  1.97; xent: 0.68; lr: 0.00044; 5095/7375 tok/s;  46009 sec
[2020-12-11 02:26:31,653 INFO] Step 40350/50000; acc:  80.92; ppl:  1.97; xent: 0.68; lr: 0.00044; 5222/7322 tok/s;  46063 sec
[2020-12-11 02:27:26,758 INFO] Step 40400/50000; acc:  80.77; ppl:  1.99; xent: 0.69; lr: 0.00044; 5209/7293 tok/s;  46119 sec
[2020-12-11 02:28:21,523 INFO] Step 40450/50000; acc:  80.87; ppl:  1.98; xent: 0.68; lr: 0.00044; 5286/7380 tok/s;  46173 sec
[2020-12-11 02:29:16,491 INFO] Step 40500/50000; acc:  80.82; ppl:  1.98; xent: 0.68; lr: 0.00044; 5165/7348 tok/s;  46228 sec
[2020-12-11 02:30:11,581 INFO] Step 40550/50000; acc:  80.84; ppl:  1.98; xent: 0.68; lr: 0.00044; 5144/7308 tok/s;  46283 sec
[2020-12-11 02:31:06,481 INFO] Step 40600/50000; acc:  80.91; ppl:  1.97; xent: 0.68; lr: 0.00044; 5054/7297 to

[2020-12-11 03:18:49,699 INFO] Step 43100/50000; acc:  81.43; ppl:  1.94; xent: 0.66; lr: 0.00043; 5188/7315 tok/s;  49201 sec
[2020-12-11 03:19:44,551 INFO] Step 43150/50000; acc:  81.42; ppl:  1.93; xent: 0.66; lr: 0.00043; 5103/7375 tok/s;  49256 sec
[2020-12-11 03:20:39,231 INFO] Step 43200/50000; acc:  81.38; ppl:  1.94; xent: 0.66; lr: 0.00043; 5137/7299 tok/s;  49311 sec
[2020-12-11 03:21:33,817 INFO] Step 43250/50000; acc:  81.53; ppl:  1.94; xent: 0.66; lr: 0.00043; 5400/7341 tok/s;  49366 sec
[2020-12-11 03:22:28,727 INFO] Step 43300/50000; acc:  81.29; ppl:  1.95; xent: 0.67; lr: 0.00042; 5195/7396 tok/s;  49420 sec
[2020-12-11 03:23:23,516 INFO] Step 43350/50000; acc:  81.61; ppl:  1.93; xent: 0.66; lr: 0.00042; 5250/7331 tok/s;  49475 sec
[2020-12-11 03:24:18,449 INFO] Step 43400/50000; acc:  81.42; ppl:  1.94; xent: 0.66; lr: 0.00042; 5071/7335 tok/s;  49530 sec
[2020-12-11 03:25:13,163 INFO] Step 43450/50000; acc:  81.36; ppl:  1.94; xent: 0.66; lr: 0.00042; 5204/7334 to

[2020-12-11 04:13:31,325 INFO] number of examples: 8014
[2020-12-11 04:13:50,184 INFO] Validation perplexity: 4.59344
[2020-12-11 04:13:50,185 INFO] Validation accuracy: 70.0959
[2020-12-11 04:14:44,841 INFO] Step 46050/50000; acc:  81.81; ppl:  1.90; xent: 0.64; lr: 0.00041; 3755/5396 tok/s;  52557 sec
[2020-12-11 04:15:39,639 INFO] Step 46100/50000; acc:  82.07; ppl:  1.90; xent: 0.64; lr: 0.00041; 5411/7329 tok/s;  52611 sec
[2020-12-11 04:16:34,408 INFO] Step 46150/50000; acc:  81.84; ppl:  1.90; xent: 0.64; lr: 0.00041; 5156/7399 tok/s;  52666 sec
[2020-12-11 04:17:29,272 INFO] Step 46200/50000; acc:  81.83; ppl:  1.91; xent: 0.64; lr: 0.00041; 5175/7337 tok/s;  52721 sec
[2020-12-11 04:18:24,037 INFO] Step 46250/50000; acc:  82.16; ppl:  1.89; xent: 0.63; lr: 0.00041; 5159/7293 tok/s;  52776 sec
[2020-12-11 04:19:18,903 INFO] Step 46300/50000; acc:  81.67; ppl:  1.91; xent: 0.65; lr: 0.00041; 5166/7379 tok/s;  52831 sec
[2020-12-11 04:20:14,073 INFO] Step 46350/50000; acc:  81.93

[2020-12-11 05:09:27,240 INFO] Step 48950/50000; acc:  82.48; ppl:  1.87; xent: 0.63; lr: 0.00040; 5366/7368 tok/s;  55839 sec
[2020-12-11 05:10:22,096 INFO] Step 49000/50000; acc:  82.38; ppl:  1.87; xent: 0.63; lr: 0.00040; 5226/7399 tok/s;  55894 sec
[2020-12-11 05:10:22,098 INFO] Loading dataset from OpenNMT-py/Data/bpe2morph/demo.valid.0.pt
[2020-12-11 05:10:22,457 INFO] number of examples: 8014
[2020-12-11 05:10:41,185 INFO] Validation perplexity: 4.5782
[2020-12-11 05:10:41,185 INFO] Validation accuracy: 70.2777
[2020-12-11 05:11:36,142 INFO] Step 49050/50000; acc:  82.42; ppl:  1.87; xent: 0.62; lr: 0.00040; 3816/5417 tok/s;  55968 sec
[2020-12-11 05:12:30,910 INFO] Step 49100/50000; acc:  82.52; ppl:  1.86; xent: 0.62; lr: 0.00040; 5116/7312 tok/s;  56023 sec
[2020-12-11 05:13:25,970 INFO] Step 49150/50000; acc:  82.22; ppl:  1.87; xent: 0.63; lr: 0.00040; 5164/7322 tok/s;  56078 sec
[2020-12-11 05:14:21,373 INFO] Step 49200/50000; acc:  82.65; ppl:  1.87; xent: 0.63; lr: 0.00

# **Translate**

Now that you have your model, you can start translating.

-model ==> Setting your model

Output predictions into pred.txt

In [16]:
!python OpenNMT-py/translate.py -model OpenNMT-py/Data/bpe2morph/model/model_step_50000.pt -src OpenNMT-py/Data/src-test-bpe.txt -output OpenNMT-py/Data/bpe2morph/pred_50k.txt -replace_unk -verbose -beam_size 1 -gpu 0

[2020-12-11 18:22:35,944 INFO] Translating shard 0.
[2020-12-11 18:22:36,783 INFO] 
SENT 1: ['"@@', '경찰의', '설명을', '보면,', '손님@@', '으로', '피@@', '시@@', '방을', '찾은', '김씨는', '다른', '손님이', '남긴', '음식@@', '물을', '자리에서', '치@@', '워@@', '달라는', '요구를', '하다', '신@@', '씨와', '말@@', '다툼을', '했다고', '한다."']
PRED 1: " According to the police 's explanation , Kim , who visited the PC room as a guest , had an argument with Shin while demanding to remove the food left by another customer from his seat . "
PRED SCORE: -0.1010

[2020-12-11 18:22:36,784 INFO] 
SENT 2: ['잠실@@', '여자@@', '고등학교@@', '(@@', '교장', '김인@@', '봉@@', ')는', '실@@', '력과', '인@@', '성을', '갖춘', '인재를', '기@@', '른@@', '다는', '지향@@', '점을', '가지고', '교사와', '학생이', '‘@@', '신뢰@@', '의', '팀@@', '플레이@@', '’를', '통해', '진로@@', '진학', '프로그램을', '업그레이드@@', '해', '나가고', '있다.']
PRED 2: " Jamsil Girls ' High School ( Principal Kim In - bong ) has upgraded its career advancement program through " " Trust Team Place " " with the aim of raising talented people with skills and pe

[2020-12-11 18:22:37,910 INFO] 
SENT 31: ['"@@', '단독', '콘서트', '무대가', '아닌,', '주', '시청@@', '층이', '청소년@@', '들인', '시상식', '무대@@', '였다는', '점에서', '화@@', '사의', '의@@', '상', '선택@@', '에는', '아쉬움이', '남@@', '는다."']
PRED 31: " It is regrettable that the main audience was the awards ceremony stage , not the solo concert stage , but the performance of the show - off . "
PRED SCORE: -0.1028

[2020-12-11 18:22:37,910 INFO] 
SENT 32: ['"@@', '추가', '취업', '희망@@', '자@@', '에다', '구직@@', '단@@', '념@@', '자,', '취업준비@@', '자', '등을', '합친', '청년@@', '층의', '잠재@@', '실업@@', '률은', '23@@', '%에', '달해', '청년', '4명', '가운데', '한', '명이', '실질적인', '실업', '상태에', '놓여', '있는', '상황이다."']
PRED 32: " The potential unemployment rate for young people , including additional job seekers , job seekers , and job seekers , reached 23 percent , with one in four young people in a real unemployment state . "
PRED SCORE: -0.0952

[2020-12-11 18:22:37,911 INFO] 
SENT 33: ['지역@@', '산업', '활력', '회복을', '위한', '단기@@', '일자리', '대책이', '포함됐다.']
PRED 33: They inc

[2020-12-11 18:22:38,581 INFO] 
SENT 61: ['이와', '달리', '우@@', '기에는', '목@@', '초가', '무성@@', '해', '구@@', '충@@', '제와', '항생@@', '제의', '수요가', '높다.']
PRED 61: " In contrast , the universe is full of wood , and the demand for oral medicine and antibiotics is high . "
PRED SCORE: -0.0935

[2020-12-11 18:22:38,581 INFO] 
SENT 62: ['대전@@', '지역', '경제가', '흔들리고', '있다는', '통계가', '지난해부터', '연이어', '나오고', '있다.']
PRED 62: Statistics have been showing that the economy in Daejeon is faltering since last year .
PRED SCORE: -0.0924

[2020-12-11 18:22:38,581 INFO] 
SENT 63: ['"남@@', '측에서는', '조용@@', '근', '육군@@', '대@@', '령@@', '과', '관련', '실무@@', '담당@@', '관', '등', '총', '4명@@', '이,', '북@@', '측에서는', '엄@@', '창@@', '남', '육군@@', '대@@', '좌@@', '와', '관련', '실무@@', '담당@@', '관', '등', '총', '4명이', '각각', '참석했다."']
PRED 63: " A total of four people from the South , including the Army Colonel Cho Yong - geun and working - level officials , attended the meeting , while a total of four from the North , including the Army Colonel Eo

[2020-12-11 18:22:39,226 INFO] 
SENT 91: ['"손@@', '석@@', '희', 'JTBC', '대표이사@@', '로부터', '폭행을', '당했다고', '주장하는', '프리랜서', '기자가', '손', '대표를', '협박@@', ',', '명예훼손', '혐의', '등으로', '검찰에', '추가', '고소@@', '했다."']
PRED 91: A freelance reporter who claims to have been assaulted by JTBC CEO Sohn Suk - hee has filed an additional complaint with the prosecution on charges of defamation and other charges against CEO Son .
PRED SCORE: -0.0977

[2020-12-11 18:22:39,227 INFO] 
SENT 92: ['경찰은', '신도@@', '들의', '휴대전화', '전원을', '끄@@', '도록', '하고', '제출받은', '뒤', '어린이@@', '들을', '포함한', '신도@@', '들의', '개인', '신원을', '일일이', '확인하고', '기록했다.']
PRED 92: " The police ordered the believers to turn off their cell phones , and then identified and recorded the identity of the congregation , including children . "
PRED SCORE: -0.0998

[2020-12-11 18:22:39,227 INFO] 
SENT 93: ['"@@', '무언@@', '가', '결@@', '심한', '박준@@', '규@@', '는', '초@@', '심을', '찾기', '위한', '극@@', '단의', '조치를', '취@@', '하게', '되는데,', '이로', '인해', '가족@@', '들@@', '간', '분위기가', 

[2020-12-11 18:22:39,920 INFO] 
SENT 121: ['그', '과정에서', '가장', '중시하는', '것은', '만@@', '화의', '특별한', '예술@@', '성에', '만화@@', '가@@', '뿐', '아니라', '모든', '국민이', '함께', '참여할', '수', '있도록', '하는', '것이다.']
PRED 121: " The most important thing in the process is to allow not only the cartoonist , but also all the people to participate together in the special artistry of comics . "
PRED SCORE: -0.0995

[2020-12-11 18:22:39,921 INFO] 
SENT 122: ['"부산@@', '과', '대구@@', '도', '각각', '76@@', '%와', '7@@', '2.9@@', '%로', '높은', '반면,', '세종@@', '은', '20@@', '.0@@', '%로', '외@@', '지인의', '토지@@', '소유', '비중이', '높은', '것으로', '나타났다."']
PRED 122: " While Busan and Daegu also had 76 % and 72.9 % , respectively , Sejong had 20.0 % of the land ownership of outsiders . "
PRED SCORE: -0.0984

[2020-12-11 18:22:39,921 INFO] 
SENT 123: ['"무@@', '차별@@', '적', '테러', '공격@@', '과', '잔@@', '혹한', '공개@@', '처@@', '형,', '자극@@', '적인', '홍보', '같은', 'IS@@', '식', '활동은', '지@@', '양@@', '하고', '보다', '부드러운', '접근', '방식을', '취하고', '있다는', '것이다."']
PRED 123:

...

[2020-12-11 18:25:47,787 INFO] 
SENT 7891: ['그중', '하나가', '도시@@', '계획을', '통한', '공동체', '조성과', '공유@@', '가치', '실현@@', '이다.']
PRED 7891: One of them is the creation of a community and the realization of shared values through urban planning .
PRED SCORE: -0.0984

[2020-12-11 18:25:47,787 INFO] 
SENT 7892: ['모든', '멤버가', '10@@', '대로', '구성된', '6@@', '인@@', '조', '그룹', '‘더', '이@@', '스트', '라이트@@', '’', '폭행', '사건의', '철저한', '수사를', '촉구하는', '국민청원', '동의', '수가', '청와대', '답변', '기준인', '20만@@', '명을', '넘어섰다.']
PRED 7892: " The number of people who petitioned for a thorough investigation into the six - member group " " The inner Light " " assault case , which consists of all 10 members , exceeded 200,000 , the standard for the presidential office 's response . "
PRED SCORE: -0.0981

[2020-12-11 18:25:47,787 INFO] 
SENT 7893: ['점유율', '1위인', '신라@@', '면이', '이', '같은', '변화에', '직격탄을', '맞@@', '았다는', '해석@@', '이다.']
PRED 7893: " Analysts say that Shin Ramyun , the No . 1 market share , was hit directly by the change .

[2020-12-11 18:25:48,445 INFO] 
SENT 7921: ['권@@', '용수', '주@@', '우즈베키스탄', '대사는', '“@@', '스마트@@', '미터', '프로젝트의', '성공', '추진을', '바탕으로', 'KT@@', '의', '우즈@@', '벡', '사업이', '다양한', 'ICT', '분야로', '확대@@', '돼', '나가@@', '기를', '바란다”고', '밝혔다.']
PRED 7921: " Kwon Yong - soo , ambassador to Uzbekistan , said , " " Based on the success of the smart meter project , I hope KT 's Uzbekistan project will expand to various ICT fields . " " "
PRED SCORE: -0.0904

[2020-12-11 18:25:48,445 INFO] 
SENT 7922: ['펑@@', '샨@@', '샨@@', '의', '뒤를', '이@@', '을', '중국', '여자', '골프@@', '의', '미래@@', '로', '불리는', '수@@', '이@@', '샹@@', '은', '특히', '쇼트@@', '게임', '능력이', '뛰@@', '나@@', '다는', '평가를', '받는다.']
PRED 7922: " Suarez , dubbed the future of Chinese women 's golf that will succeed Feng Shanshan , is particularly considered to have played a short game capability . "
PRED SCORE: -0.0962

[2020-12-11 18:25:48,445 INFO] 
SENT 7923: ['영어가', '정규', '교과@@', '로', '편성@@', '되는', '것은', '초등학교', '3@@', '학년@@', '부터다.']
PRED 7923: It is from t

[2020-12-11 18:25:49,132 INFO] 
SENT 7951: ['카타@@', '르는', '4@@', '경기@@', '서', '10@@', '골을', '허용@@', '했을', '정도로', '수비가', '약한', '팀@@', '이기', '때문에', '정상적으로', '상대@@', '하면', '충분히', '이길', '수', '있는', '상대@@', '다.']
PRED 7951: " Qatar is a weak team with so much defense that it allowed 10 goals in four games , so it is a opponent who can win if they face normal . "
PRED SCORE: -0.0962

[2020-12-11 18:25:49,132 INFO] 
SENT 7952: ['대상@@', '㈜@@', '에서', '제조@@', '한', '청정@@', '원', '‘@@', '런@@', '천@@', '미@@', '트@@', '’의', '일부', '제품에서', '세균이', '검출@@', '돼', '식품의약품안전@@', '처@@', '로부터', '판매', '중단', '및', '회수@@', '조치', '판정을', '받았다.']
PRED 7952: " Germs were detected in some of the products of the " " Luncheon Meat " " manufactured by Daesang Co. , Ltd. , which was declared suspended sales and recalled by the Ministry of Food and Drug Safety . "
PRED SCORE: -0.0928

[2020-12-11 18:25:49,132 INFO] 
SENT 7953: ['"강@@', '씨', '등은', '김씨가', '휴대전화', '가@@', '개통', '이후', '판매', '대금', '일부를', '가로@@', '챘@@', '다는', '이유로', '

[2020-12-11 18:25:49,823 INFO] 
SENT 7981: ['"@@', '근대@@', '건축물', '기록@@', '보존@@', '사업은', '지난', '2010년부터', '광주시가', '추진하고', '있는', '사업@@', '으로,', '그동안', '사업@@', '대상', '건물@@', '주의', '비@@', '협조@@', '와', '건축물', '산@@', '재로', '사업@@', '추진에', '적지', '않은', '어려움을', '겪@@', '었다."']
PRED 7981: " The modern building Records Preservation Project is a project that the Gwangju Metropolitan City has been pushing for since 2010 , which has suffered considerable difficulties in promoting the project due to the non - cooperation of building owners and building constructions . "
PRED SCORE: -0.0947

[2020-12-11 18:25:49,824 INFO] 
SENT 7982: ['보도에', '따르면', '방', '전', '대표', '주변@@', '인들은', '방', '전', '대표가', '장', '씨와', '2008@@', '년@@', '∼@@', '2009@@', '년에', '잠시', '동안', '자주', '만나는', '사이@@', '였으며', '방', '대표가', '장', '씨를', '언급@@', '하기도', '했다고', '진술했다.']
PRED 7982: " According to reports , people around former representative Bang testified that former representative Bang had frequently met with Jang for a while between

[2020-12-11 18:25:50,338 INFO] 
SENT 8011: ['다만', '북미가', '공동', '유해@@', '발굴', '사업에', '합의@@', '한다면', '미국', '장비@@', '의', '대북', '반입@@', '과', '발굴', '비용', '지@@', '불', '등을', '위한', '대북제재', '예외', '인@@', '정이', '필요하다.']
PRED 8011: " However , if North Korea and the U.S. agree on a joint excavation project , it is necessary to designate an exception to sanctions against North Korea for the import of U.S. equipment to North Korea and the payment of the cost of excavation . "
PRED SCORE: -0.1052

[2020-12-11 18:25:50,338 INFO] 
SENT 8012: ['출산@@', '과', '육아@@', '에', '대한', '부담이', '부모에게', '지나치게', '쏠리는', '환경을', '개선@@', '하지', '않으면', '저출산', '문제를', '해결하는', '건', '요원@@', '하다.']
PRED 8012: " If the government does not improve the environment in which the burden of childbirth and childcare is too much on parents , it is far from solving the problem of low birth rates . "
PRED SCORE: -0.0996

[2020-12-11 18:25:50,339 INFO] 
SENT 8013: ['여기', '국내', '론@@', '칭', '이후', '누적@@', '판매', '10만@@', '대를', '돌파한', '유모@@', '차


# Detokenization

Even after the translation process is finished, it is still in a segment, so it is different from the actual sentence structure used by real people. Thus, when you perform a detoxification process, it is returned in the form of the actual sentence.

We Use "sed" for BPE Detokenization


In [8]:
!sed -i "s/@@ //g"  OpenNMT-py/Data/morph2bpe/pred.txt

# Post-processing

In [7]:
f = open('OpenNMT-py/Data/tgt-test-morph.txt', 'r', encoding='utf-8')
txt = f.read()
# txt = txt.replace(' ', '')
# txt = txt.replace('ᴥ', ' ')

with open("OpenNMT-py/Data/tgt-test-morph-edited.txt", "w") as f:
    f.write(txt)
    
txt[:1000]

'" According to descriptions by the police , Mr. Kim , who visited the PC - bang as a guest , had an argument with Mr. Shin while demanding that food left by other guests be cleared from his seat . " \n" As Jamsil Girls \' High School ( Principal Kim In - bong ) is aiming to cultivate talents and good personality , the teachers and students are upgrading their career path programs through the " " Team - play of Trust " " . " \nFormer lawmaker Kim will lose both his right to vote and his right to run for 5 years if a fine of 1 million won or more is confirmed . \n" The working environment of Daejeon Industrial Park in Daedeok - gu , Daejeon will be improved . " \n" Around 90 t of reinforcement facilities were lost due to high waves at the Dongbang Breakwater Construction site in Wimi Port , Namwon - eup , Seogwipo - si , and a 100 m median strip fell in the area of Nohyeong Rotary - Samsung Service Center in Jeju . " \nIt is a program to make students value physical education and art . 

In [8]:
f = open('OpenNMT-py/Data/bpe2morph/pred_10k.txt', 'r', encoding='utf-8')
txt = f.read()
# txt = txt.replace(' ', '')
# txt = txt.replace('ᴥ', ' ')

with open("OpenNMT-py/Data/bpe2char/pred_10k-edited.txt", "w") as f:
    f.write(txt)

f = open('OpenNMT-py/Data/bpe2char/pred_10k-edited.txt', 'r', encoding='utf-8')
txt = f.read()
txt[:1000]  

'" According to the police \'s explanation , Kim , who visited the pizza restaurant with a guest , said he had a quarrel with Shin while asking for the food left by another guest at the spot . "\n" Jamsil Girls \' High School ( Principal Kim In - bong ) is adding up career advancement programs through " " Trust \'s Team Play " " with the aim of giving talent with skills and personality . "\n" If the sentence of more than 1 million won is confirmed , former lawmaker Kim will lose both the election and the right to vote for five years . "\n" The working environment of Daejeon Industrial Complex in Daedeok - gu , Daejeon will be improved . "\n" About 90 tons of reinforced facilities were distributed at the Eastern Port of the Port of the Port of the Port of the Port of the Port of Mireuksa - eup , Seogwipo - si , and the median strip of 100 m fell down in the area of the Jeju - Samsung Service Center . "\nIt is a program aimed at ensuring students to value sports and art .\n" The U.S. Jus

# Evaluation Using BLEU

Quantitative evaluation is performed on the sentence thus obtained. BLEU is a quantitative evaluation method for machine translation. You can see which model is superior by comparing it to the BLEU score you are comparing.

https://www.aclweb.org/anthology/P02-1040

In [17]:
!perl  OpenNMT-py/tools/multi-bleu.perl OpenNMT-py/Data/tgt-test-morph.txt < OpenNMT-py/Data/bpe2morph/pred_50k.txt

BLEU = 35.73, 67.5/43.0/29.0/20.6 (BP=0.985, ratio=0.985, hyp_len=276207, ref_len=280287)
